In [1]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
import os

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity='all'
%load_ext autoreload
%matplotlib inline

sns.set_style('whitegrid')
sns.set_palette('viridis')

In [2]:
os.listdir('./patents/')

['sampleSubmission.csv', 'test_data.csv', 'train_data.csv']

In [3]:
patent_files = [i for i in os.listdir('D:Downloads2/patents/patents/') ]

In [73]:
len(patent_files)

4972

In [5]:
submission_ids = pd.read_csv('./patents/test_data.csv')

In [6]:
train_file_ids = pd.read_csv('./patents/train_data.csv')

In [7]:
train_file_ids.head()

id first_ipc_mark_section
0   0                      A
1   1                      G
2   2                      A
3   3                      A
4   4                      D

In [8]:
# fn = patent_files[5]

# with open('./patents/patents/' + fn) as f:
# #     t = f.read()
#     t = f.readlines()  # I was using this to eyeball the patents manually for CLUES to cool features

In [9]:
# fn = patent_files[5]

# with open('./patents/patents/' + fn) as f:
#     t = f.read()
# #     t = f.readlines()  # I was using this to eyeball the patents manually for CLUES to cool features
# # t

In [10]:
# train_file_ids = train_file_ids[:400] # start small time
# train_file_ids = train_file_ids[train_file_ids.first_ipc_mark_section.isin(['A', 'G'])] # start small time

In [11]:
train_file_ids.first_ipc_mark_section.value_counts()

A    1303
G     781
C     637
B     442
H     330
E     287
F     178
D      14
Name: first_ipc_mark_section, dtype: int64

In [12]:
len(patent_files)
train_file_ids.shape

4972

(3972, 2)

In [13]:
# train_file_ids.id

In [14]:
#  put them all together
big_df = pd.concat([train_file_ids, submission_ids], ignore_index=True)

In [15]:
%%time
big_df['raw_txt_complt'] = big_df['id'].apply(lambda x: 
         open('D:Downloads2/patents/patents/' + str(x) + '.txt',
              encoding='latin8').read()) # will this leave all the files hanging open???

Wall time: 1min 9s


In [16]:
# failed_files = big_df[big_df.raw_txt_complt.apply(
#     lambda x: 'parse failure' in x)].copy()

# failed_files.shape

In [17]:
big_df.raw_txt_complt[0].split('\n\n\n')[0]

'                                            ABSTRACT\n\n  The disclosure relates to a method for gradually coloring hair comprising the steps of:        a)\n\n  applying an air oxidation haircolor composition to hair; b) removing the air oxidation haircolor\n\n5 composition from the hair directly after application; and c) repeating a set comprising the steps\n\n  a) and b) in multiple spaced intervals. The air oxidation haircolor composition can include: 1)\n\n  at least one primary oxidation dye intermediate; 2) at least one aromatic triol; and 3) water.'

In [18]:
# big_df.raw_txt_complt.apply(lambda x: x.split('CLAIMS DEFINING')[1] if ('CLAIMS DEFINING' in x) else None)

In [19]:
# [i[:100] for i in big_df.raw_txt_complt[0].split('\n\n\n')]

In [20]:
# big_df['abstract'] = big_df['raw_txt_complt'].apply(lambda x: x.split('\n\n\n')[0])

In [21]:
pd.options.display.max_colwidth = 200

In [22]:
big_df.head(2)

first_ipc_mark_section  id  \
0                      A   0   
1                      G   1   

                                                                                                                                                                                            raw_txt_complt  
0                                              ABSTRACT\n\n  The disclosure relates to a method for gradually coloring hair comprising the steps of:        a)\n\n  applying an air oxidation haircolor...  
1                                             ABSTRACT\n\n       A system and method are provided for executing multilateral transactional bookkeeping\n\nworkflows between a plurality of participants...

In [23]:
big_df.raw_txt_complt.apply(lambda x: len(x)).sort_values(ascending=False)[:4]

980     11136188
463      7972691
456      5308704
1407     4801126
Name: raw_txt_complt, dtype: int64

In [24]:
big_df[big_df.raw_txt_complt.apply(lambda x: '<U+' in x)].raw_txt_complt.apply(lambda x: len(x))[:10]

16     38912
20     10837
21     39522
26     53090
33     12219
37     23388
38    413298
40     78826
41     37285
43     43092
Name: raw_txt_complt, dtype: int64

In [25]:
big_df['len_after_tables'] = big_df.raw_txt_complt.apply(lambda x: len(x.split('  <U+')[1]) if ('  <U+' in x) else 0)

In [26]:
big_df.tail(2)

first_ipc_mark_section    id  \
4970                    NaN  4970   
4971                    NaN  4971   

                                                                                                                                                                                               raw_txt_complt  \
4970                                         ABSTRACT\n\nA molded shoe sole comprising a plurality of protruding elements on the lower\n\nsurface of the sole configured to create channels for fluid flow...   
4971                                                -31\n\n                                           Abstract\n\n   A gaming system is disclosed which is arranged to\n\n   implement a base game and a f...   

      len_after_tables  
4970                92  
4971                 0

In [27]:
big_df['len_abstract'] = big_df.raw_txt_complt.apply(lambda x: len(x.split('\n\n\n')[0]))

In [28]:
big_df['raw_txt_trunc'] = big_df.raw_txt_complt.apply(lambda x: x.split('<U+')[0] if ('  <U+' in x) else x)

In [29]:
big_df['raw_txt_trunc'] = big_df.raw_txt_trunc.apply(lambda x: x.split('removed-apn')[0] if ('removed-apn' in x) else x)

In [30]:
big_df['raw_txt_trunc'] = big_df.raw_txt_trunc.apply(lambda x: x.split('TTGG')[0] if ('TTGG' in x) else x)

In [31]:
big_df['raw_txt_trunc'] = big_df.raw_txt_trunc.apply(lambda x: x.split('ttgg')[0] if ('ttgg' in x) else x)

In [32]:
big_df['raw_txt_trunc'] = big_df.raw_txt_trunc.apply(lambda x: x.split('::::')[0] if ('::::' in x) else x)

In [33]:
big_df['raw_txt_trunc'] = big_df.raw_txt_trunc.apply(lambda x: x.split('Abbreviations')[0] if ('Abbreviations' in x) else x)

In [34]:
big_df['raw_txt_trunc'] = big_df.raw_txt_trunc.apply(lambda x: x[:10000])

In [35]:
# big_df.raw_txt_trunc

In [36]:
big_df.head(3)

first_ipc_mark_section  id  \
0                      A   0   
1                      G   1   
2                      A   2   

                                                                                                                                                                                            raw_txt_complt  \
0                                              ABSTRACT\n\n  The disclosure relates to a method for gradually coloring hair comprising the steps of:        a)\n\n  applying an air oxidation haircolor...   
1                                             ABSTRACT\n\n       A system and method are provided for executing multilateral transactional bookkeeping\n\nworkflows between a plurality of participants...   
2                                             ABSTRACT\n\nA media module 10 for use with at least one item of furniture includes a body member 16\n\nconfigured to be mounted adjacent the at least one...   

   len_after_tables  len_abstract  \
0                 0           551   
1                 0           523   
2                 0           752   

                                                                                                                                                                                             raw_txt_trunc  
0                                              ABSTRACT\n\n  The disclosure relates to a method for gradually coloring hair comprising the steps of:        a)\n\n  applying an air oxidation haircolor...  
1                                             ABSTRACT\n\n       A system and method are provided for executing multilateral transactional bookkeeping\n\nworkflows between a plurality of participants...  
2                                             ABSTRACT\n\nA media module 10 for use with at least one item of furniture includes a body member 16\n\nconfigured to be mounted adjacent the at least one...

In [37]:
# sns.distplot(big_df.raw_txt_trunc.apply(lambda x: len(x)).sort_values(ascending=False))

In [38]:
# len(big_df.raw_txt_trunc.iloc[296].split('provides therapeutic proteins ')[0])

In [39]:
# big_df.raw_txt_trunc.iloc[1407].split('removed-apn')[1]

In [40]:
# train_file_ids.raw_txt_complt[0]

## Gensim

In [41]:
from gensim import corpora, models
from gensim.models.doc2vec import TaggedDocument
from sklearn.feature_extraction import stop_words

from nltk.stem.snowball import SnowballStemmer
from nltk import sent_tokenize, word_tokenize, bigrams
import re

C:\Users\Alistair\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [42]:
stemmer = SnowballStemmer("english")

In [45]:
['_'.join(i) for i in list(bigrams(['la', 'lady', 'free']))]

['la_lady', 'lady_free']

In [57]:
def tokenize_and_stem(text):
    tokens = [word for sent in sent_tokenize(text) for word in word_tokenize(sent) 
              if (word not in stop_words.ENGLISH_STOP_WORDS)]
    bigrams_ = ['_'.join(i) for i in list(bigrams(tokens))]
    tokens.extend(bigrams_)
    filtered_tokens = []
    for token in tokens:
        if re.search('[a-zA-Z]', token):
            filtered_tokens.append(token)
    stems = [stemmer.stem(t) for t in filtered_tokens]
    return stems

In [47]:
def tag_docs(docs):
    tagged = docs.apply(lambda r:
                        TaggedDocument(words=tokenize_and_stem(r['raw_txt_trunc']),
                                       tags=[r.first_ipc_mark_section]), axis=1)
    return tagged

In [48]:
def train_doc2vec_model(tagged_docs, window=5, size=1000, iter=5,
                        min_count=5, ):
    sents = tagged_docs.values
    doc2vec_model = models.Doc2Vec(sents, size=size, window=window, min_count=min_count,
                                   iter=iter, dm=1)
    return doc2vec_model

In [49]:
def vec_for_learning(doc2vec_model, tagged_docs):
    sents = tagged_docs.values
    targets, regressors = zip(*[(doc.tags[0], doc2vec_model.infer_vector(doc.words, steps=20)) for doc in sents])
    return targets, regressors

In [50]:
from sklearn.model_selection import train_test_split, GridSearchCV

In [51]:
from sklearn.linear_model import LogisticRegression, LogisticRegressionCV

In [52]:
from sklearn.svm import SVC

In [53]:
# weight_dict = dict(big_df.first_ipc_mark_section.value_counts().apply(lambda x: 100/x))

In [54]:
# n_obs = 500

# smaller_df = big_df.sample(n=n_obs, replace=False
# weights = big_df.first_ipc_mark_section[:n_obs].map(weight_dict))

In [55]:
# big_df[:3972]

In [58]:
# %%time
# train_data, test_data = train_test_split(big_df[:3972])
# train_data, test_data = train_test_split(big_df, train_size=3972)

train_tagged = tag_docs(big_df[:39])

In [60]:
%%time
# train_data, test_data = train_test_split(big_df[:3972])
# train_data, test_data = train_test_split(big_df, train_size=3972)

train_tagged = tag_docs(big_df[:3972])

In [79]:
%%time
test_tagged = tag_docs(big_df[3972:]) # for submission

Wall time: 33.3 s


In [62]:
%%time
model = train_doc2vec_model(train_tagged, iter=50, size=500)

C:\Users\Alistair\Anaconda3\lib\site-packages\gensim\models\doc2vec.py:362: UserWarning: The parameter `iter` is deprecated, will be removed in 4.0.0, use `epochs` instead.
  warnings.warn("The parameter `iter` is deprecated, will be removed in 4.0.0, use `epochs` instead.")
C:\Users\Alistair\Anaconda3\lib\site-packages\gensim\models\doc2vec.py:366: UserWarning: The parameter `size` is deprecated, will be removed in 4.0.0, use `vector_size` instead.
  warnings.warn("The parameter `size` is deprecated, will be removed in 4.0.0, use `vector_size` instead.")


Wall time: 5min 56s


In [63]:
y_train, X_train = vec_for_learning(model, train_tagged)

In [77]:
# y_test, X_test = vec_for_learning(model, test_tagged)

In [65]:
# from sklearn.metrics import f1_score

In [66]:
# f1_score(y_test, y_pred, average='micro')

In [303]:
pd.Series(y_train).value_counts()

A    1303
G     781
C     637
B     442
H     330
E     287
F     178
D      14
dtype: int64

In [67]:
logregCV = LogisticRegressionCV(Cs=[0.001, 0.01, 1, 10], cv=5,
                                multi_class='ovr',
                                penalty='l2', refit=True,
                                scoring='f1_micro', solver='liblinear'
                               )

In [68]:
%%time
logregCV.fit(X_train, y_train)

Wall time: 32.5 s


LogisticRegressionCV(Cs=[0.001, 0.01, 1, 10], class_weight=None, cv=5,
           dual=False, fit_intercept=True, intercept_scaling=1.0,
           max_iter=100, multi_class='ovr', n_jobs=1, penalty='l2',
           random_state=None, refit=True, scoring='f1_micro',
           solver='liblinear', tol=0.0001, verbose=0)

In [69]:
logregCV.scores_

{'A': array([[0.79824561, 0.86842105, 0.84962406, 0.82330827],
        [0.80175659, 0.89084065, 0.88080301, 0.85570891],
        [0.75692695, 0.83123426, 0.83501259, 0.79596977],
        [0.76388889, 0.83712121, 0.84217172, 0.81944444],
        [0.74841972, 0.83944374, 0.82300885, 0.80025284]]),
 'B': array([[0.89598997, 0.96616541, 0.96616541, 0.94360902],
        [0.89962359, 0.9749059 , 0.96863237, 0.95608532],
        [0.90176322, 0.96473552, 0.96851385, 0.95214106],
        [0.89520202, 0.95328283, 0.96085859, 0.94570707],
        [0.90265487, 0.97092288, 0.97597977, 0.95954488]]),
 'C': array([[0.85087719, 0.94360902, 0.93483709, 0.9160401 ],
        [0.84818068, 0.93475533, 0.92471769, 0.91342535],
        [0.84130982, 0.9256927 , 0.89672544, 0.8790932 ],
        [0.84217172, 0.93686869, 0.93686869, 0.91792929],
        [0.86346397, 0.93426043, 0.93678887, 0.90897598]]),
 'D': array([[0.9962406 , 0.9962406 , 1.        , 1.        ],
        [0.99623588, 0.99623588, 1.        , 1

In [322]:
y_preds_ovr = logregCV.predict(X_test)

In [70]:
logregCV_multi = LogisticRegressionCV(Cs=[0.001, 0.01, 1, 10], cv=5,
                                multi_class='multinomial',
                                refit=True,
                                scoring='f1_micro', )

In [71]:
%%time
logregCV_multi.fit(X_train, y_train)

Wall time: 17.7 s


LogisticRegressionCV(Cs=[0.001, 0.01, 1, 10], class_weight=None, cv=5,
           dual=False, fit_intercept=True, intercept_scaling=1.0,
           max_iter=100, multi_class='multinomial', n_jobs=1, penalty='l2',
           random_state=None, refit=True, scoring='f1_micro',
           solver='lbfgs', tol=0.0001, verbose=0)

In [72]:
logregCV_multi.scores_

{'A': array([[0.80952381, 0.84461153, 0.78070175, 0.74686717],
        [0.81430364, 0.86951066, 0.82434128, 0.78920954],
        [0.80730479, 0.83627204, 0.76826196, 0.7279597 ],
        [0.80176768, 0.84090909, 0.77020202, 0.75252525],
        [0.83817952, 0.87610619, 0.79013906, 0.75094817]]),
 'B': array([[0.80952381, 0.84461153, 0.78070175, 0.74686717],
        [0.81430364, 0.86951066, 0.82434128, 0.78920954],
        [0.80730479, 0.83627204, 0.76826196, 0.7279597 ],
        [0.80176768, 0.84090909, 0.77020202, 0.75252525],
        [0.83817952, 0.87610619, 0.79013906, 0.75094817]]),
 'C': array([[0.80952381, 0.84461153, 0.78070175, 0.74686717],
        [0.81430364, 0.86951066, 0.82434128, 0.78920954],
        [0.80730479, 0.83627204, 0.76826196, 0.7279597 ],
        [0.80176768, 0.84090909, 0.77020202, 0.75252525],
        [0.83817952, 0.87610619, 0.79013906, 0.75094817]]),
 'D': array([[0.80952381, 0.84461153, 0.78070175, 0.74686717],
        [0.81430364, 0.86951066, 0.82434128, 0

In [335]:
# %%time
# param_grid = {'C': [1e2, 1e3, 1e4],
#               'gamma': [ 0.0005, 0.001, 0.05], }
# clf = GridSearchCV(SVC(kernel='rbf', class_weight='balanced'),
#                    param_grid, cv=3, scoring='f1_micro',
#                   verbose=1)
# clf = clf.fit(X_train, y_train)
# print("Best estimator found by grid search:")
# print(clf.best_estimator_)

In [336]:
# SVC_preds = clf.predict(X_test)

In [337]:
# clf.best_params_

In [339]:
# clf.best_score_

In [80]:
%%time
y_test, X_test = vec_for_learning(model, test_tagged)

Wall time: 1min 5s


In [81]:
multinom_preds = logregCV_multi.predict(X_test)

In [82]:
submission_ids.head()

id
0  3972
1  3973
2  3974
3  3975
4  3976

In [330]:
# submission_ids['first_ipc_mark_section'] = SVC_preds
# submission_ids.to_csv('vanilla_SVC_with_Doc2Vec.csv', index=False)
# submission_ids['first_ipc_mark_section'] = y_preds
# submission_ids.to_csv('vanilla_logregCV_with_Doc2Vec.csv', index=False)

In [39]:
# %%time
# texts = train_file_ids.abstract.fillna('and').apply(lambda x: tokenize_and_stem(x))

In [65]:
# %%time
# texts = big_df[:30].apply(lambda x: 
#                             TaggedDocument(words=tokenize_and_stem(x['raw_txt_complt']),
#                                            tags=x['first_ipc_mark_section']), 1)

In [66]:
# %%time
# texts = big_df.abstract.apply(lambda x: tokenize_and_stem(x))

In [50]:
import datetime

In [51]:
# texts.to_csv('tokenised_and_stemmed_all_files_{}.csv'.format(str(datetime.datetime.now())[:13]))

In [52]:
# texts = pd.read_csv('tokenised_and_stemmed_all_files_2018-10-14 20.csv', header=None)[1]

In [53]:
texts[:4]

0    ([abstract, the, disclosur, relat, method, gradual, color, hair, compris, step, appli, air, oxid, haircolor, composit, hair, b, remov, air, oxid, haircolor, composit, hair, direct, applic, c, repe...
1    ([abstract, a, method, provid, execut, multilater, transact, bookkeep, workflow, plural, particip, includ, receiv, previous, agre, formal, rule, receiv, author, decis, evolv, agreement, base, auth...
2    ([abstract, a, media, modul, use, item, furnitur, includ, bodi, member, configur, mount, adjac, item, furnitur, bodi, member, defin, plural, surfac, a, storag, compart, open, surfac, bodi, member,...
3    ([abstract, a, support, garment, have, flexibl, panel, have, connect, portion, second, oppos, connect, portion, plural, strap, extend, connect, portion, plural, strap, have, end, portion, attach, ...
dtype: object

In [54]:
texts.shape

(30,)

In [55]:
sents = texts.values

In [56]:
model = models.Doc2Vec(sents, size=200, iter=5)

C:\Users\Alistair\Anaconda3\lib\site-packages\gensim\models\doc2vec.py:362: UserWarning: The parameter `iter` is deprecated, will be removed in 4.0.0, use `epochs` instead.
  warnings.warn("The parameter `iter` is deprecated, will be removed in 4.0.0, use `epochs` instead.")
C:\Users\Alistair\Anaconda3\lib\site-packages\gensim\models\doc2vec.py:366: UserWarning: The parameter `size` is deprecated, will be removed in 4.0.0, use `vector_size` instead.
  warnings.warn("The parameter `size` is deprecated, will be removed in 4.0.0, use `vector_size` instead.")


In [57]:
model.docvecs.count

7

In [58]:
targets, regressors = zip(*[(doc.tags[0],
                             model.infer_vector(doc.words, steps=20))
                            for doc in sents])

In [42]:
# Build the bigram and trigram models
bigram = models.Phrases(texts, min_count=5, threshold=100) # higher threshold fewer phrases.
# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = models.phrases.Phraser(bigram)

In [43]:
%%time
bigram_vec = [bigram_mod[doc] for doc in texts]

Wall time: 904 ms


In [44]:
# bigram_vec[:3]

In [45]:
dictionary = corpora.Dictionary(bigram_vec)
corpus = [dictionary.doc2bow(text) for text in bigram_vec]

In [46]:
# print(corpus[0])

In [47]:
import gensim.sklearn_api as gen_sk

In [48]:
model = gen_sk.D2VTransformer(min_count=5, size=3000, max_vocab_size=None,
                              hs=1, iter=10, sample=0.001)

In [49]:
%%time
docvecs = model.fit_transform(bigram_vec)

C:\Users\Alistair\Anaconda3\lib\site-packages\gensim\models\doc2vec.py:362: UserWarning: The parameter `iter` is deprecated, will be removed in 4.0.0, use `epochs` instead.
  warnings.warn("The parameter `iter` is deprecated, will be removed in 4.0.0, use `epochs` instead.")
C:\Users\Alistair\Anaconda3\lib\site-packages\gensim\models\doc2vec.py:366: UserWarning: The parameter `size` is deprecated, will be removed in 4.0.0, use `vector_size` instead.
  warnings.warn("The parameter `size` is deprecated, will be removed in 4.0.0, use `vector_size` instead.")


Wall time: 1min 3s


In [50]:
docvecs

array([[ 0.14307429,  0.10900369, -0.06645241, ...,  0.04153612,
         0.00374449,  0.02259251],
       [ 0.09393291,  0.03853409,  0.02769088, ...,  0.01324915,
         0.08030222, -0.0642508 ],
       [ 0.02471516,  0.01807155, -0.22840424, ...,  0.01491266,
         0.02898922,  0.19297329],
       ...,
       [-0.04650203, -0.01477077,  0.01415239, ...,  0.00857414,
         0.003771  ,  0.01798538],
       [-0.18505278, -0.20226921,  0.4016656 , ..., -0.07283975,
         0.05929404, -0.00047601],
       [-0.12017289,  0.1644588 ,  0.00513491, ...,  0.04339314,
         0.03490079,  0.22748679]], dtype=float32)

In [51]:
docvecs.shape

(4972, 3000)

In [52]:
big_df[big_df.first_ipc_mark_section.isnull()==False].shape

(3972, 4)

In [53]:
big_df.shape
big_df.id.max()

(4972, 4)

4971

In [55]:
docvecs[:3972].shape

(4972, 3000)

In [63]:
local_data      = docvecs[:3972]
submission_data = docvecs[3972:]

In [64]:
from sklearn.preprocessing import LabelEncoder

In [65]:
encoder = LabelEncoder()

In [66]:
encoded_target = encoder.fit_transform(big_df.first_ipc_mark_section.dropna())

In [67]:
len(encoded_target)

3972

In [68]:
from sklearn.model_selection import train_test_split, RandomizedSearchCV

X_train, X_test, y_train, y_test = train_test_split(local_data, encoded_target,
                                                    test_size=0.1, random_state=42)

In [69]:
from sklearn import cross_validation

In [70]:
import scipy.stats as stats

In [71]:
import xgboost as xgb

In [ ]:
%%time
clf_xgb = xgb.XGBClassifier(objective = 'mlogloss' )
param_dist = {'n_estimators': stats.randint(150, 500),
              'learning_rate': stats.uniform(0.01, 0.07),
              'subsample': stats.uniform(0.3, 0.7),
              'max_depth': [3, 4, 5, 6, 7, 8, 9],
              'colsample_bytree': stats.uniform(0.5, 0.45),
              'min_child_weight': [1, 2, 3]
             }
clf = RandomizedSearchCV(clf_xgb, param_distributions = param_dist, cv=2,
                         n_iter = 3, scoring = 'f1_micro',
                         error_score = 0, verbose = 3, n_jobs = -1)

clf.fit(X_train, y_train)

Fitting 2 folds for each of 3 candidates, totalling 6 fits


[Parallel(n_jobs=-1)]: Done   2 out of   6 | elapsed:  8.8min remaining: 17.7min


In [ ]:
clf.best_score_

In [ ]:
clf.best_params_

In [134]:
clf.best_params_

{'colsample_bytree': 0.7843064079591726,
 'learning_rate': 0.040818002464485345,
 'max_depth': 7,
 'min_child_weight': 3,
 'n_estimators': 234,
 'subsample': 0.5995044435864736}

In [104]:
good_model = 

In [112]:
big_df.columns

Index(['first_ipc_mark_section', 'id', 'raw_txt_complt', 'abstract'], dtype='object')

In [113]:
submission_ids['first_ipc_mark_section'] = encoder.inverse_transform(good_model.predict(submission_data))

C:\Users\Alistair\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\Alistair\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:


In [115]:
submission_ids.to_csv('first_sub_doc2vec_abstracts_only.csv', index=False)

In [116]:
dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_test, label=y_test)

In [124]:
param = {
    'n_estimators': 200,
    'max_depth': 5,  # the maximum depth of each tree
    'eta': 0.1,  # the training step for each iteration
    'silent': 1,  # logging mode - quiet
    'objective': 'multi:softprob',  # error evaluation for multiclass training
    'num_class': 8}  # the number of classes that exist in this datset
num_round = 200  # the number of training iterations

In [125]:
trained_xgb = xgb.train(params=param, dtrain=dtrain,
                        num_boost_round=num_round, verbose_eval=3)

In [126]:
preds = trained_xgb.predict(dtest)

In [127]:
f1_score(y_test, np.argmax(preds, 1), average='micro')

0.375

In [128]:
data_dmatrix = xgb.DMatrix(data=X_train,label=y_train)

In [129]:
cv_results = xgb.cv(dtrain=data_dmatrix, params=param, nfold=3,
                    num_boost_round=50,early_stopping_rounds=10,metrics="mlogloss", 
                    as_pandas=True, seed=123)

In [130]:
cv_results

test-mlogloss-mean  test-mlogloss-std  train-mlogloss-mean  \
0            2.014948           0.020141             1.932820   
1            1.986122           0.048361             1.802712   
2            1.959409           0.063520             1.684569   
3            1.920764           0.086545             1.578468   
4            1.889773           0.105937             1.481983   
5            1.863774           0.111383             1.389397   
6            1.845320           0.124442             1.305648   
7            1.842245           0.132910             1.232263   

   train-mlogloss-std  
0            0.002572  
1            0.003904  
2            0.004282  
3            0.007747  
4            0.012582  
5            0.013593  
6            0.015959  
7            0.022618

In [131]:
# tfidf = models.TfidfModel(corpus)

In [277]:
# %%time
# model_embeddings = models.Word2Vec(bigram_vec, min_count=5, size=150,
#                                    workers=4, window=5, iter=100)

# model_embeddings.vector_size

# model_embeddings.most_similar('juic')

In [278]:
# list(model_embeddings.wv.vocab.keys())

In [287]:
%%time
ldamodel = models.ldamodel.LdaModel(tfidf[corpus],
                                    num_topics=200, id2word = dictionary, passes=50)

C:\Users\Alistair\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Alistair\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Alistair\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

Wall time: 7min 58s


In [288]:
# ldamodel.get_document_topics()

In [289]:
print(ldamodel.print_topics(num_topics=5))
# corpus_lda = ldamodel[corpus]

[(122, '0.000*"2-methyl-4-phenoxyphenyl" + 0.000*"2-methoxyethylamino" + 0.000*"2-methyl-5-nitrophenylcarbam" + 0.000*"2-methyl-5-nitrophenyl" + 0.000*"2-methyl-5-nitroanilin" + 0.000*"2-methyl-5-" + 0.000*"2-methyl-4_phenoxyphenyl" + 0.000*"2-methyl-4-phenoxyphenylboron" + 0.000*"2-methylpropyl" + 0.000*"2-methoxyethanol"'), (198, '0.002*"damper" + 0.002*"target_criteria" + 0.001*"advertis" + 0.001*"sheath" + 0.001*"bid" + 0.001*"cathet" + 0.000*"line_a-a" + 0.000*"hub" + 0.000*"unidirect" + 0.000*"bump"'), (27, '0.000*"2-methyl-4-phenoxyphenyl" + 0.000*"2-methoxyethylamino" + 0.000*"2-methyl-5-nitrophenylcarbam" + 0.000*"2-methyl-5-nitrophenyl" + 0.000*"2-methyl-5-nitroanilin" + 0.000*"2-methyl-5-" + 0.000*"2-methyl-4_phenoxyphenyl" + 0.000*"2-methyl-4-phenoxyphenylboron" + 0.000*"2-methylpropyl" + 0.000*"2-methoxyethanol"'), (97, '0.000*"2-methyl-4-phenoxyphenyl" + 0.000*"2-methoxyethylamino" + 0.000*"2-methyl-5-nitrophenylcarbam" + 0.000*"2-methyl-5-nitrophenyl" + 0.000*"2-methyl-5

In [ ]:
import pyLDAvis
import pyLDAvis.gensim

pyLDAvis.enable_notebook()

In [ ]:
%%time
vis = pyLDAvis.gensim.prepare(ldamodel, tfidf[corpus], dictionary)

In [ ]:
# tfidf[corpus]

In [ ]:
vis.topic_coordinates['x'] = vis.topic_coordinates['x'].apply(lambda x: x.real)
vis.topic_coordinates['y'] = vis.topic_coordinates['y'].apply(lambda x: x.real)

In [ ]:
vis

In [ ]:
%%time
cast_topics = pd.DataFrame(np.vstack([np.array(i)[:,1] 
                                      for i in ldamodel.get_document_topics(bow=tfidf[corpus],
                                                                            minimum_probability=0)]),
                           columns=['topic_'+str(i+1) for i in range(ldamodel.num_topics)])

print(cast_topics.shape)

In [ ]:
# viscast

In [ ]:
cast_topics

In [237]:
import xgboost